In [1]:
import pandas as pd
import numpy as np
import pymongo

In [2]:
df=pd.read_csv("gun-violence-data_01-2013_03-2018.csv.zip")

In [3]:
conn = 'mongodb://localhost:27017'
client = pymongo.MongoClient(conn)
# Declare the database
db = client.guns_db
# Declare the collection
guns = db.guns

In [4]:
client.list_database_names()

['admin',
 'classDB',
 'config',
 'craigslist_db',
 'dumpster_db',
 'guns_db',
 'local',
 'mars_db',
 'store_inventory',
 'team_db',
 'travel_db']

In [5]:
df.columns

Index(['incident_id', 'date', 'state', 'city_or_county', 'address', 'n_killed',
       'n_injured', 'incident_url', 'source_url',
       'incident_url_fields_missing', 'congressional_district', 'gun_stolen',
       'gun_type', 'incident_characteristics', 'latitude',
       'location_description', 'longitude', 'n_guns_involved', 'notes',
       'participant_age', 'participant_age_group', 'participant_gender',
       'participant_name', 'participant_relationship', 'participant_status',
       'participant_type', 'sources', 'state_house_district',
       'state_senate_district'],
      dtype='object')

In [6]:
dropped_columns=df.drop(columns=['city_or_county','address','incident_url','source_url','incident_url_fields_missing','congressional_district','gun_stolen','gun_type','incident_characteristics','location_description','n_guns_involved','notes','participant_age','participant_age_group','participant_name','participant_relationship','participant_status','participant_type','sources','state_house_district','state_senate_district','participant_gender'])

In [7]:
dropped_columns

incident_id        date           state  n_killed  n_injured  \
0            461105  2013-01-01    Pennsylvania         0          4   
1            460726  2013-01-01      California         1          3   
2            478855  2013-01-01            Ohio         1          3   
3            478925  2013-01-05        Colorado         4          0   
4            478959  2013-01-07  North Carolina         2          2   
...             ...         ...             ...       ...        ...   
239672      1083142  2018-03-31       Louisiana         0          0   
239673      1083139  2018-03-31       Louisiana         1          0   
239674      1083151  2018-03-31       Louisiana         0          1   
239675      1082514  2018-03-31           Texas         1          0   
239676      1081940  2018-03-31           Maine         2          0   

        latitude  longitude  
0        40.3467   -79.8559  
1        33.9090  -118.3330  
2        41.4455   -82.1377  
3        39.6518  -104.8020  
4        36.1140   -79.9569  
...          ...        ...  
239672       NaN        NaN  
239673   31.7537   -93.0836  
239674   29.9239   -90.0442  
239675   29.7201   -95.6110  
239676   44.7293   -69.7691  

[239677 rows x 7 columns]

In [8]:
clean = dropped_columns.loc[(dropped_columns['state'] == "Pennsylvania") | (dropped_columns['state'] == "Tennessee") | (dropped_columns['state'] == "California")]

In [9]:
clean

incident_id        date         state  n_killed  n_injured  latitude  \
0            461105  2013-01-01  Pennsylvania         0          4   40.3467   
1            460726  2013-01-01    California         1          3   33.9090   
8            479389  2013-01-21    California         0          4   37.9656   
10           491674  2013-01-23     Tennessee         1          3   35.0221   
15           479573  2013-02-02     Tennessee         0          5   35.0803   
...             ...         ...           ...       ...        ...       ...   
239655      1082089  2018-03-31    California         0          0   32.8936   
239657      1082394  2018-03-31    California         0          0   35.5019   
239658      1082392  2018-03-31    California         1          0       NaN   
239660      1082091  2018-03-31    California         2          0   37.9478   
239667      1082234  2018-03-31     Tennessee         0          1   35.2045   

        longitude  
0        -79.8559  
1       -118.3330  
8       -121.7180  
10       -85.2697  
15       -89.8871  
...           ...  
239655  -117.1360  
239657  -119.2830  
239658        NaN  
239660  -121.3140  
239667   -89.9872  

[32861 rows x 7 columns]

In [10]:
guns_df=clean.dropna()

In [11]:
gun=guns_df['date'] >= '2015-01-01'

In [12]:
guns_df= guns_df[gun]

In [13]:
guns_df.to_dict('records')

[{'incident_id': 272502,
  'date': '2015-01-01',
  'state': 'Tennessee',
  'n_killed': 0,
  'n_injured': 1,
  'latitude': 35.0064,
  'longitude': -85.3179},
 {'incident_id': 271979,
  'date': '2015-01-01',
  'state': 'California',
  'n_killed': 1,
  'n_injured': 2,
  'latitude': 34.0322,
  'longitude': -117.32600000000001},
 {'incident_id': 273937,
  'date': '2015-01-01',
  'state': 'Pennsylvania',
  'n_killed': 1,
  'n_injured': 0,
  'latitude': 39.8449,
  'longitude': -75.3816},
 {'incident_id': 272960,
  'date': '2015-01-01',
  'state': 'Pennsylvania',
  'n_killed': 1,
  'n_injured': 0,
  'latitude': 39.8406,
  'longitude': -75.3976},
 {'incident_id': 272551,
  'date': '2015-01-01',
  'state': 'California',
  'n_killed': 1,
  'n_injured': 0,
  'latitude': 37.3006,
  'longitude': -120.49799999999999},
 {'incident_id': 272555,
  'date': '2015-01-01',
  'state': 'California',
  'n_killed': 0,
  'n_injured': 0,
  'latitude': 36.6121,
  'longitude': -121.836},
 {'incident_id': 273336,
  

In [14]:
guns.insert_many(guns_df.to_dict('records'))

In [18]:
results=guns.find()

In [19]:
 data = []
for result in results:
    row = dict(result)
    if "_id" in row:
        del row["_id"]
    print(row)
    data.append(row)
        

{'incident_id': 272502, 'date': '2015-01-01', 'state': 'Tennessee', 'n_killed': 0, 'n_injured': 1, 'latitude': 35.0064, 'longitude': -85.3179}
{'incident_id': 271979, 'date': '2015-01-01', 'state': 'California', 'n_killed': 1, 'n_injured': 2, 'latitude': 34.0322, 'longitude': -117.32600000000001}
{'incident_id': 273937, 'date': '2015-01-01', 'state': 'Pennsylvania', 'n_killed': 1, 'n_injured': 0, 'latitude': 39.8449, 'longitude': -75.3816}
{'incident_id': 272960, 'date': '2015-01-01', 'state': 'Pennsylvania', 'n_killed': 1, 'n_injured': 0, 'latitude': 39.8406, 'longitude': -75.3976}
{'incident_id': 272551, 'date': '2015-01-01', 'state': 'California', 'n_killed': 1, 'n_injured': 0, 'latitude': 37.3006, 'longitude': -120.49799999999999}
{'incident_id': 272555, 'date': '2015-01-01', 'state': 'California', 'n_killed': 0, 'n_injured': 0, 'latitude': 36.6121, 'longitude': -121.836}
{'incident_id': 273336, 'date': '2015-01-01', 'state': 'Pennsylvania', 'n_killed': 0, 'n_injured': 1, 'latitude

{'incident_id': 274951, 'date': '2015-01-06', 'state': 'Pennsylvania', 'n_killed': 1, 'n_injured': 0, 'latitude': 40.4134, 'longitude': -79.9914}
{'incident_id': 791137, 'date': '2015-01-06', 'state': 'California', 'n_killed': 1, 'n_injured': 0, 'latitude': 37.9304, 'longitude': -121.291}
{'incident_id': 275091, 'date': '2015-01-06', 'state': 'Tennessee', 'n_killed': 0, 'n_injured': 1, 'latitude': 35.2075, 'longitude': -89.9943}
{'incident_id': 275072, 'date': '2015-01-06', 'state': 'Tennessee', 'n_killed': 0, 'n_injured': 1, 'latitude': 35.0137, 'longitude': -85.2823}
{'incident_id': 274605, 'date': '2015-01-06', 'state': 'Tennessee', 'n_killed': 0, 'n_injured': 1, 'latitude': 35.9727, 'longitude': -83.9074}
{'incident_id': 275034, 'date': '2015-01-06', 'state': 'California', 'n_killed': 0, 'n_injured': 1, 'latitude': 37.696999999999996, 'longitude': -122.126}
{'incident_id': 277318, 'date': '2015-01-06', 'state': 'California', 'n_killed': 0, 'n_injured': 0, 'latitude': 37.3715, 'long

{'incident_id': 338151, 'date': '2015-05-08', 'state': 'California', 'n_killed': 0, 'n_injured': 0, 'latitude': 36.8084, 'longitude': -119.82600000000001}
{'incident_id': 336883, 'date': '2015-05-08', 'state': 'Pennsylvania', 'n_killed': 0, 'n_injured': 0, 'latitude': 40.4944, 'longitude': -79.9156}
{'incident_id': 392932, 'date': '2015-05-08', 'state': 'California', 'n_killed': 0, 'n_injured': 0, 'latitude': 37.6652, 'longitude': -122.398}
{'incident_id': 337411, 'date': '2015-05-08', 'state': 'Pennsylvania', 'n_killed': 0, 'n_injured': 0, 'latitude': 40.9716, 'longitude': -77.7221}
{'incident_id': 336347, 'date': '2015-05-08', 'state': 'California', 'n_killed': 1, 'n_injured': 0, 'latitude': 33.8732, 'longitude': -118.05}
{'incident_id': 336866, 'date': '2015-05-08', 'state': 'Pennsylvania', 'n_killed': 1, 'n_injured': 0, 'latitude': 39.9171, 'longitude': -75.2529}
{'incident_id': 337006, 'date': '2015-05-08', 'state': 'California', 'n_killed': 0, 'n_injured': 0, 'latitude': 36.2059,

{'incident_id': 390255, 'date': '2015-08-07', 'state': 'Tennessee', 'n_killed': 0, 'n_injured': 0, 'latitude': 35.9753, 'longitude': -86.5124}
{'incident_id': 391632, 'date': '2015-08-07', 'state': 'California', 'n_killed': 1, 'n_injured': 1, 'latitude': 36.6828, 'longitude': -121.648}
{'incident_id': 523018, 'date': '2015-08-07', 'state': 'Pennsylvania', 'n_killed': 0, 'n_injured': 0, 'latitude': 40.0375, 'longitude': -76.3093}
{'incident_id': 389920, 'date': '2015-08-07', 'state': 'Pennsylvania', 'n_killed': 0, 'n_injured': 0, 'latitude': 39.9191, 'longitude': -75.1585}
{'incident_id': 390187, 'date': '2015-08-07', 'state': 'California', 'n_killed': 1, 'n_injured': 0, 'latitude': 34.9509, 'longitude': -120.431}
{'incident_id': 389914, 'date': '2015-08-07', 'state': 'Pennsylvania', 'n_killed': 0, 'n_injured': 1, 'latitude': 39.9669, 'longitude': -75.2299}
{'incident_id': 390491, 'date': '2015-08-07', 'state': 'Pennsylvania', 'n_killed': 1, 'n_injured': 2, 'latitude': 39.995, 'longitud

{'incident_id': 438585, 'date': '2015-10-26', 'state': 'Tennessee', 'n_killed': 0, 'n_injured': 1, 'latitude': 35.2179, 'longitude': -90.0105}
{'incident_id': 437549, 'date': '2015-10-26', 'state': 'Pennsylvania', 'n_killed': 0, 'n_injured': 2, 'latitude': 39.8446, 'longitude': -75.5382}
{'incident_id': 618437, 'date': '2015-10-26', 'state': 'Pennsylvania', 'n_killed': 0, 'n_injured': 0, 'latitude': 40.688, 'longitude': -75.2222}
{'incident_id': 437407, 'date': '2015-10-26', 'state': 'Pennsylvania', 'n_killed': 0, 'n_injured': 0, 'latitude': 40.5991, 'longitude': -75.3783}
{'incident_id': 436634, 'date': '2015-10-26', 'state': 'Pennsylvania', 'n_killed': 1, 'n_injured': 0, 'latitude': 39.9937, 'longitude': -75.1778}
{'incident_id': 436620, 'date': '2015-10-26', 'state': 'Pennsylvania', 'n_killed': 1, 'n_injured': 0, 'latitude': 40.4384, 'longitude': -79.9863}
{'incident_id': 437401, 'date': '2015-10-26', 'state': 'Pennsylvania', 'n_killed': 0, 'n_injured': 0, 'latitude': 39.8957, 'long

...

{'incident_id': 900549, 'date': '2017-07-27', 'state': 'Pennsylvania', 'n_killed': 0, 'n_injured': 0, 'latitude': 40.3448, 'longitude': -78.9571}
{'incident_id': 900608, 'date': '2017-07-27', 'state': 'California', 'n_killed': 1, 'n_injured': 0, 'latitude': 34.0205, 'longitude': -117.31700000000001}
{'incident_id': 900921, 'date': '2017-07-27', 'state': 'Tennessee', 'n_killed': 0, 'n_injured': 2, 'latitude': 35.5887, 'longitude': -87.0409}
{'incident_id': 899575, 'date': '2017-07-27', 'state': 'California', 'n_killed': 0, 'n_injured': 0, 'latitude': 37.8057, 'longitude': -122.235}
{'incident_id': 900071, 'date': '2017-07-27', 'state': 'California', 'n_killed': 0, 'n_injured': 0, 'latitude': 38.5345, 'longitude': -121.46799999999999}
{'incident_id': 900760, 'date': '2017-07-27', 'state': 'Pennsylvania', 'n_killed': 1, 'n_injured': 0, 'latitude': 40.0542, 'longitude': -75.1432}
{'incident_id': 900617, 'date': '2017-07-27', 'state': 'Tennessee', 'n_killed': 0, 'n_injured': 0, 'latitude': 

{'incident_id': 931555, 'date': '2017-09-10', 'state': 'California', 'n_killed': 1, 'n_injured': 1, 'latitude': 36.7251, 'longitude': -121.656}
{'incident_id': 931553, 'date': '2017-09-10', 'state': 'California', 'n_killed': 0, 'n_injured': 0, 'latitude': 36.7671, 'longitude': -121.75399999999999}
{'incident_id': 931000, 'date': '2017-09-10', 'state': 'California', 'n_killed': 1, 'n_injured': 1, 'latitude': 34.1866, 'longitude': -118.465}
{'incident_id': 930260, 'date': '2017-09-10', 'state': 'California', 'n_killed': 0, 'n_injured': 2, 'latitude': 37.8404, 'longitude': -122.26100000000001}
{'incident_id': 930255, 'date': '2017-09-10', 'state': 'California', 'n_killed': 0, 'n_injured': 1, 'latitude': 34.0435, 'longitude': -118.351}
{'incident_id': 930997, 'date': '2017-09-10', 'state': 'California', 'n_killed': 2, 'n_injured': 0, 'latitude': 33.8619, 'longitude': -118.14200000000001}
{'incident_id': 932445, 'date': '2017-09-10', 'state': 'California', 'n_killed': 0, 'n_injured': 0, 'la

{'incident_id': 978025, 'date': '2017-10-23', 'state': 'California', 'n_killed': 0, 'n_injured': 0, 'latitude': 34.2437, 'longitude': -116.831}
{'incident_id': 971423, 'date': '2017-10-23', 'state': 'Pennsylvania', 'n_killed': 0, 'n_injured': 1, 'latitude': 39.9492, 'longitude': -75.2416}
{'incident_id': 966555, 'date': '2017-10-23', 'state': 'Pennsylvania', 'n_killed': 1, 'n_injured': 0, 'latitude': 40.4537, 'longitude': -79.8888}
{'incident_id': 986367, 'date': '2017-10-23', 'state': 'California', 'n_killed': 1, 'n_injured': 0, 'latitude': 34.0809, 'longitude': -118.051}
{'incident_id': 972421, 'date': '2017-10-23', 'state': 'California', 'n_killed': 1, 'n_injured': 0, 'latitude': 38.0115, 'longitude': -121.818}
{'incident_id': 966925, 'date': '2017-10-23', 'state': 'California', 'n_killed': 1, 'n_injured': 0, 'latitude': 38.145, 'longitude': -121.27600000000001}
{'incident_id': 966850, 'date': '2017-10-23', 'state': 'Tennessee', 'n_killed': 1, 'n_injured': 0, 'latitude': 35.0064, 'l

{'incident_id': 1013192, 'date': '2017-12-22', 'state': 'Tennessee', 'n_killed': 1, 'n_injured': 0, 'latitude': 35.0885, 'longitude': -89.9211}
{'incident_id': 1033014, 'date': '2017-12-22', 'state': 'Pennsylvania', 'n_killed': 0, 'n_injured': 0, 'latitude': 42.1131, 'longitude': -80.0955}
{'incident_id': 1012470, 'date': '2017-12-22', 'state': 'California', 'n_killed': 0, 'n_injured': 0, 'latitude': 40.6572, 'longitude': -124.212}
{'incident_id': 1015775, 'date': '2017-12-22', 'state': 'California', 'n_killed': 0, 'n_injured': 2, 'latitude': 37.4707, 'longitude': -122.211}
{'incident_id': 1015961, 'date': '2017-12-22', 'state': 'California', 'n_killed': 0, 'n_injured': 0, 'latitude': 37.9579, 'longitude': -121.315}
{'incident_id': 1015971, 'date': '2017-12-22', 'state': 'California', 'n_killed': 0, 'n_injured': 1, 'latitude': 38.0272, 'longitude': -121.34299999999999}
{'incident_id': 1015982, 'date': '2017-12-22', 'state': 'California', 'n_killed': 0, 'n_injured': 0, 'latitude': 38.02

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [20]:
print(data)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

